In [1]:
case class LogRecord( host:String, timestamp:String, url:String, httpCode: Int)

defined class LogRecord


In [2]:
val pattern = """^(\S+) \S+ \S+ \[([\w:/]+ \S\d{4})\] "\S+ ([\w./-]+) \S+" (\d{3}) \S+$""".r 

pattern = ^(\S+) \S+ \S+ \[([\w:/]+ \S\d{4})\] "\S+ ([\w./-]+) \S+" (\d{3}) \S+$


^(\S+) \S+ \S+ \[([\w:/]+ \S\d{4})\] "\S+ ([\w./-]+) \S+" (\d{3}) \S+$

In [3]:
def parseLogLine(line:String):
    LogRecord = {
             val res = pattern.findFirstMatchIn(line)
             if (res.isEmpty)
             {   
                 println("Rejected Log Line:" + line)
                 LogRecord("Empty", "", "", -1)
              }
              else
              {  
                 val m = res.get
                 LogRecord(m.group(1), m.group(2), m.group(3), m.group(4).toInt)
               }
          }

parseLogLine: (line: String)LogRecord


In [4]:
var line1 = """uplherc.upl.com - - [01/Aug/1995:00:00:08 -0400] "GET /images/ksclogo-medium.gif HTTP/1.0" 304 0"""

line1 = uplherc.upl.com - - [01/Aug/1995:00:00:08 -0400] "GET /images/ksclogo-medium.gif HTTP/1.0" 304 0


uplherc.upl.com - - [01/Aug/1995:00:00:08 -0400] "GET /images/ksclogo-medium.gif HTTP/1.0" 304 0

In [5]:
parseLogLine(line1)

LogRecord(uplherc.upl.com,01/Aug/1995:00:00:08 -0400,/images/ksclogo-medium.gif,304)

In [6]:
var logs = sc.textFile("/data/spark/project/NASA_access_log_Aug95.gz")

logs = /data/spark/project/NASA_access_log_Aug95.gz MapPartitionsRDD[1] at textFile at <console>:27


/data/spark/project/NASA_access_log_Aug95.gz MapPartitionsRDD[1] at textFile at <console>:27

Rejected Log Line:www-c3.proxy.aol.com - - [01/Aug/1995:00:00:57 -0400] "GET /cgi-bin/imagemap/countdown70?285,291 HTTP/1.0" 302 85
Rejected Log Line:205.163.36.61 - - [01/Aug/1995:00:02:10 -0400] "GET /cgi-bin/imagemap/countdown70?342,281 HTTP/1.0" 302 98
Rejected Log Line:rpgopher.aist.go.jp - - [01/Aug/1995:00:02:45 -0400] "GET /cgi-bin/imagemap/countdown70?181,275 HTTP/1.0" 302 110
Rejected Log Line:rpgopher.aist.go.jp - - [01/Aug/1995:00:04:05 -0400] "GET /cgi-bin/imagemap/countdown70?51,156 HTTP/1.0" 302 111
Rejected Log Line:haraway.ucet.ufl.edu - - [01/Aug/1995:00:04:47 -0400] "GET /cgi-bin/imagemap/countdown70?199,165 HTTP/1.0" 302 97
Rejected Log Line:rpgopher.aist.go.jp - - [01/Aug/1995:00:04:47 -0400] "GET /cgi-bin/imagemap/countdown70?54,211 HTTP/1.0" 302 110
Rejected Log Line:haraway.ucet.ufl.edu - - [01/Aug/1995:00:04:55 -0400] "GET /cgi-bin/imagemap/fr?264,412 HTTP/1.0" 302 91
Rejected Log Line:ad11-061.compuserve.com - - [01/Aug/1995:00:08:42 -0400] "GET /cgi-bin/image

In [7]:
var parseLogs = logs.map(parseLogLine)

parseLogs = MapPartitionsRDD[2] at map at <console>:35


MapPartitionsRDD[2] at map at <console>:35

In [8]:
var logDf = parseLogs.toDF()

logDf = [host: string, timestamp: string ... 2 more fields]


[host: string, timestamp: string ... 2 more fields]

In [9]:
logDf.printSchema 

root
 |-- host: string (nullable = true)
 |-- timestamp: string (nullable = true)
 |-- url: string (nullable = true)
 |-- httpCode: integer (nullable = true)



In [10]:
logDf.createOrReplaceTempView("nasalog")

In [11]:
val output = spark.sql("select * from nasalog")

output = [host: string, timestamp: string ... 2 more fields]


[host: string, timestamp: string ... 2 more fields]

In [12]:
output.createOrReplaceTempView("nasa_log")

In [13]:
spark.sql("cache TABLE nasa_log")

[]

In [14]:
spark.sql("select url, count(*) as req_cnt from nasa_log where upper(url) like '%HTML%' group by url order by req_cnt desc limit 10").show

[Stage 3:====================>                                  (76 + 56) / 200]+--------------------+-------+
|                 url|req_cnt|
+--------------------+-------+
|           /ksc.html|  43615|
|/shuttle/missions...|  24580|
|/shuttle/missions...|  22425|
|/software/winvn/w...|  10337|
|/history/history....|  10110|
|/history/apollo/a...|   8973|
|/shuttle/countdow...|   7856|
|/history/apollo/a...|   7158|
|/shuttle/technolo...|   6504|
|/shuttle/missions...|   5260|
+--------------------+-------+



In [15]:
spark.sql("select substr(timestamp, 1, 14) as timeFrame, count(*) as req_cnt from nasa_log group by substr(timestamp, 1, 14) order by req_cnt desc limit 5").show

+--------------+-------+
|     timeFrame|req_cnt|
+--------------+-------+
|              |  31889|
|31/Aug/1995:11|   6160|
|31/Aug/1995:10|   6078|
|31/Aug/1995:13|   5815|
|30/Aug/1995:15|   5755|
+--------------+-------+



In [16]:
spark.sql("select substr(timestamp, 1, 14) as timeFrame, count(*) as req_cnt from nasa_log group by substr(timestamp, 1, 14) order by req_cnt limit 5").show

+--------------+-------+
|     timeFrame|req_cnt|
+--------------+-------+
|03/Aug/1995:04|     16|
|03/Aug/1995:09|     22|
|03/Aug/1995:05|     43|
|03/Aug/1995:10|     57|
|03/Aug/1995:07|     58|
+--------------+-------+



In [17]:
spark.sql("select distinct httpCode as HTTP_code, count(*) as cnt from nasa_log group by httpCode order by cnt desc").show

+---------+-------+
|HTTP_code|    cnt|
+---------+-------+
|      200|1390479|
|      304| 134138|
|       -1|  31889|
|      404|   9424|
|      302|   3767|
|      403|    171|
|      501|     27|
|      500|      3|
+---------+-------+

